In [1]:
import pandas as pd
from pandas import DataFrame
from scipy.stats import zscore
import numpy as np
from numpy import mean
from numpy import std
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.model_selection import KFold
from matplotlib import pyplot
from itertools import combinations
from pandas import DataFrame
from sklearn.preprocessing import PolynomialFeatures
from sklearn.ensemble import GradientBoostingRegressor
import xgboost as xgb
from sklearn.datasets import load_boston
from sklearn.model_selection import train_test_split
from sklearn.model_selection import cross_val_score, KFold
from sklearn.metrics import mean_squared_error
import matplotlib.pyplot as plt
from sklearn.model_selection import RepeatedKFold
from numpy import absolute


In [2]:
# Definitions used
def get_dataset():
    df = pd.read_excel('new_df_66.xlsx', engine='openpyxl')
    new_df_1 = df.drop(['ile', 'ile_st', 'trp', 'trp_st', 'h_pi', 'X.w'], axis=1)
    X = new_df_1.drop(['DELTA30'], axis=1)
    Y = new_df_1['DELTA30']
    return X, Y

def get_models():
    models = dict()
    for d in range(1,4):
        trans = PolynomialFeatures(degree=d)
        model = GradientBoostingRegressor(verbose=0)
        models[str(d)] = Pipeline(steps=[('t', trans), ('m', model)])
    return models

def evaluate_model(model, X, Y):
    kfold = KFold(n_splits=num_instances, random_state=seed)
    n_scores = cross_val_score(model, X, Y, cv=kfold, scoring=scoring)
    return n_scores

# Use PolynomialFeatures in sklearn.preprocessing to create two-way interactions for all features
def add_interactions(df):
    # Get feature names
    combos = list(combinations(list(df.columns), 2))
    colnames = list(df.columns) + ['_'.join(x) for x in combos]

    # Find interactions
    poly = PolynomialFeatures(interaction_only=True, include_bias=False)
    df = poly.fit_transform(df)
    df = pd.DataFrame(df)
    df.columns = colnames

    # Remove interaction terms with all 0 values
    noint_indicies = [i for i, x in enumerate(list((df == 0).all())) if x]
    df = df.drop(df.columns[noint_indicies], axis=1)

    return df


In [3]:
#Removing empty columns and splitting X and Y from the rest of the dataset
df = pd.read_excel('new_df_66.xlsx', engine='openpyxl')
new_df_1 = df.drop(['ile', 'ile_st', 'trp', 'trp_st', 'h_pi', 'X.w', 'MSWHIM3.1','DELTA30', 'PP2.1'], axis=1)
Y = df['DELTA30']

In [4]:
#% removing correlated features
correlated_features= set()
correlation_matrix = new_df_1.corr()
for i in range(len(correlation_matrix.columns)):
    for j in range(i):
        if abs(correlation_matrix.iloc[i, j]) > 0.90:
            colname = correlation_matrix.columns[i]
            correlated_features.add(colname)

In [5]:
correlated_features

{'BLOSUM1.1',
 'F2.1',
 'KF2.1',
 'KF4.1',
 'MSWHIM1.1',
 'ProtFP1.1',
 'ProtFP2.1',
 'ST1.1',
 'T1.1',
 'VHSE1.1',
 'VHSE3.1',
 'VHSE5.1',
 'as_max_dst',
 'as_max_dst_st',
 'convex_hull_volume',
 'glu_st',
 'leu_st',
 'mean_as_solv_acc_st',
 'met_st',
 'phe_st',
 'pock_asa',
 'pock_asa22',
 'pock_asa_st',
 'pock_pol_asa',
 'prop_polar_atm_st',
 'rmsd_bs_ca',
 'rmsd_bs_ca_sd',
 'rmsd_pro_bb',
 'rmsd_pro_bb_st',
 'rmsd_pro_ca',
 'rmsd_pro_ca_sd',
 'rog_bs_bb',
 'rog_bs_bb_sd',
 'rog_bs_ca',
 'rog_bs_ca_sd',
 'rog_bs_noh',
 'rog_bs_noh_sd',
 'rog_pro_bb',
 'rog_pro_bb_sd',
 'rog_pro_ca',
 'rog_pro_ca_sd',
 'rog_pro_noh_sd',
 'volume_score_st'}

In [6]:
# new_df_1.drop(correlated_features, axis=1, inplace=True)
# new_df_1

In [7]:
new_df_1.describe()

pock_volume  pock_volume_st    pock_asa  pock_asa_st  pock_pol_asa  \
count   312.000000      312.000000  312.000000   312.000000    312.000000   
mean    429.389885      138.224801  271.705718    81.541548    154.255801   
std      61.382677       15.601207   39.506842     9.765166     24.920249   
min     254.248000       91.690000  155.087000    53.443000     87.169000   
25%     391.977750      127.408500  247.380500    75.351750    139.288750   
50%     437.454000      137.356000  274.197000    80.828500    155.019000   
75%     468.571000      148.297750  294.710750    86.869500    170.112000   
max     597.876000      179.463000  394.394000   112.650000    230.699000   

       pock_pol_asa_st  pock_apol_asa  pock_apol_asa_st  pock_asa22  \
count       312.000000     312.000000        312.000000  312.000000   
mean         50.041442     117.449955         41.318638  145.666744   
std           6.345904      19.969150          5.175438   20.699041   
min          30.329000      61.692000         24.929000   89.519000   
25%          46.135750     104.827000         37.719250  130.574500   
50%          49.393500     117.058500         41.465500  147.289500   
75%          54.254750     129.559250         44.933750  158.565500   
max          71.484000     180.835000         57.720000  204.401000   

       pock_asa22_st  ...   BLOSUM3.1   BLOSUM4.1   BLOSUM5.1   BLOSUM6.1  \
count     312.000000  ...  312.000000  312.000000  312.000000  312.000000   
mean       54.044343  ...  -13.124968   -1.511667   -8.649712   22.815481   
std         5.468378  ...    1.113859    0.729112    1.173283    1.040080   
min        38.210000  ...  -15.800000   -3.230000  -12.430000   19.780000   
25%        50.637250  ...  -13.760000   -2.010000   -9.290000   22.227500   
50%        53.716000  ...  -13.435000   -1.680000   -8.500000   22.580000   
75%        57.460750  ...  -12.505000   -1.137500   -7.820000   23.200000   
max        69.722000  ...   -8.750000    1.140000   -5.800000   26.480000   

        BLOSUM7.1   BLOSUM8.1   BLOSUM9.1  BLOSUM10.1   MSWHIM1.1   MSWHIM2.1  
count  312.000000  312.000000  312.000000  312.000000  312.000000  312.000000  
mean    10.862179   -3.110929   18.961378   16.639679  -63.650577   98.337051  
std      1.122445    1.564785    0.954909    1.114765    1.087187    0.987445  
min      6.700000  -10.510000   16.370000   13.120000  -66.860000   95.840000  
25%     10.280000   -3.885000   18.347500   15.922500  -64.200000   97.787500  
50%     11.050000   -2.950000   18.850000   16.800000  -63.850000   98.350000  
75%     11.345000   -2.090000   19.620000   17.397500  -63.055000   98.727500  
max     14.480000    0.130000   21.810000   19.010000  -60.210000  103.750000  

[8 rows x 186 columns]

In [8]:
# histograms of the variables
new_df_1.hist(figsize=(200,200))
pyplot.show()

C:\Users\Nick\AppData\Roaming\Python\Python37\site-packages\pandas\plotting\_matplotlib\tools.py:331: MatplotlibDeprecationWarning: 
The is_first_col function was deprecated in Matplotlib 3.4 and will be removed two minor releases later. Use ax.get_subplotspec().is_first_col() instead.
  if ax.is_first_col():


In [9]:
from sklearn.preprocessing import PowerTransformer
pt = PowerTransformer(method='yeo-johnson')
data = pt.fit_transform(new_df_1)
data = DataFrame(data)
data.hist(figsize=(200,200))
pyplot.show()


C:\Users\Nick\AppData\Roaming\Python\Python37\site-packages\sklearn\preprocessing\_data.py:2995: RuntimeWarning: divide by zero encountered in log
  loglike = -n_samples / 2 * np.log(x_trans.var())
C:\Users\Nick\AppData\Roaming\Python\Python37\site-packages\sklearn\preprocessing\_data.py:2960: RuntimeWarning: overflow encountered in power
  out[pos] = (np.power(x[pos] + 1, lmbda) - 1) / lmbda
C:\Users\Nick\miniconda3\envs\torch\lib\site-packages\numpy\core\_methods.py:195: RuntimeWarning: overflow encountered in multiply
  x = um.multiply(x, x, out=x)
C:\Users\Nick\miniconda3\envs\torch\lib\site-packages\numpy\core\_methods.py:199: RuntimeWarning: overflow encountered in reduce
  ret = umr_sum(x, axis, dtype, out, keepdims)
C:\Users\Nick\AppData\Roaming\Python\Python37\site-packages\pandas\plotting\_matplotlib\tools.py:331: MatplotlibDeprecationWarning: 
The is_first_col function was deprecated in Matplotlib 3.4 and will be removed two minor releases later. Use ax.get_subplotspec().is_

In [10]:
data.describe()


0             1             2             3             4    \
count  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02   
mean  -1.209191e-16  1.693802e-16  5.492401e-16  5.300247e-16  3.420519e-16   
std    1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00   
min   -2.534060e+00 -3.246842e+00 -2.710560e+00 -3.355171e+00 -2.644464e+00   
25%   -6.506842e-01 -6.805013e-01 -6.419668e-01 -6.091271e-01 -6.072222e-01   
50%    8.552383e-02 -2.903922e-02  3.176870e-02 -2.546861e-02  2.314806e-02   
75%    6.200334e-01  6.621816e-01  5.669348e-01  5.823790e-01  6.335859e-01   
max    3.096474e+00  2.508181e+00  3.390293e+00  2.844761e+00  3.131248e+00   

                5             6             7             8             9    \
count  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02   
mean   1.023042e-16  1.014146e-16 -7.419279e-17 -3.651148e-16  1.465752e-15   
std    1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00   
min   -3.437255e+00 -2.778356e+00 -3.247899e+00 -2.642704e+00 -3.079700e+00   
25%   -5.980757e-01 -6.348123e-01 -6.924481e-01 -7.367205e-01 -6.112113e-01   
50%   -7.291824e-02 -2.200969e-02  3.563061e-02  6.780349e-02 -3.949586e-02   
75%    6.815591e-01  6.061027e-01  7.029475e-01  6.185548e-01  6.381443e-01   
max    3.129239e+00  3.198547e+00  3.115406e+00  2.915746e+00  2.739704e+00   

       ...           176           177           178           179  \
count  ...  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02   
mean   ... -3.061120e-16 -4.981770e-17 -1.715152e-15 -5.208932e-10   
std    ...  1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00   
min    ... -3.397914e+00 -3.209078e+00 -2.688531e+00 -4.425535e+00   
25%    ... -5.238429e-01 -6.887405e-01 -6.096362e-01 -5.189082e-01   
50%    ... -1.739576e-01 -1.296583e-01  5.046639e-02 -1.258063e-01   
75%    ...  6.900849e-01  6.712171e-01  6.800486e-01  4.918462e-01   
max    ...  2.627780e+00  2.427584e+00  3.010917e+00  2.660765e+00   

                180           181           182           183           184  \
count  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02   
mean   1.100259e-15 -6.476301e-17 -2.586962e-15  3.917806e-16  1.839696e-16   
std    1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00   
min   -3.394447e+00 -3.327902e+00 -2.811915e+00 -2.402391e+00 -3.156276e+00   
25%   -5.408273e-01 -6.093871e-01 -6.359302e-01 -7.419341e-01 -4.895878e-01   
50%    1.441778e-01 -2.871712e-02 -1.033992e-01  3.491162e-02 -1.610016e-01   
75%    4.128514e-01  6.016009e-01  6.979394e-01  6.514358e-01  5.667845e-01   
max    3.470691e+00  3.257280e+00  2.888041e+00  2.727678e+00  2.967846e+00   

              185  
count  312.000000  
mean    -0.026578  
std      1.001253  
min     -2.863891  
25%     -0.566367  
50%      0.042745  
75%      0.427446  
max      4.659166  

[8 rows x 186 columns]

In [11]:
cols = new_df_1.columns.tolist()
data.columns = cols
data.describe()

pock_volume  pock_volume_st      pock_asa   pock_asa_st  pock_pol_asa  \
count  3.120000e+02    3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02   
mean  -1.209191e-16    1.693802e-16  5.492401e-16  5.300247e-16  3.420519e-16   
std    1.001606e+00    1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00   
min   -2.534060e+00   -3.246842e+00 -2.710560e+00 -3.355171e+00 -2.644464e+00   
25%   -6.506842e-01   -6.805013e-01 -6.419668e-01 -6.091271e-01 -6.072222e-01   
50%    8.552383e-02   -2.903922e-02  3.176870e-02 -2.546861e-02  2.314806e-02   
75%    6.200334e-01    6.621816e-01  5.669348e-01  5.823790e-01  6.335859e-01   
max    3.096474e+00    2.508181e+00  3.390293e+00  2.844761e+00  3.131248e+00   

       pock_pol_asa_st  pock_apol_asa  pock_apol_asa_st    pock_asa22  \
count     3.120000e+02   3.120000e+02      3.120000e+02  3.120000e+02   
mean      1.023042e-16   1.014146e-16     -7.419279e-17 -3.651148e-16   
std       1.001606e+00   1.001606e+00      1.001606e+00  1.001606e+00   
min      -3.437255e+00  -2.778356e+00     -3.247899e+00 -2.642704e+00   
25%      -5.980757e-01  -6.348123e-01     -6.924481e-01 -7.367205e-01   
50%      -7.291824e-02  -2.200969e-02      3.563061e-02  6.780349e-02   
75%       6.815591e-01   6.061027e-01      7.029475e-01  6.185548e-01   
max       3.129239e+00   3.198547e+00      3.115406e+00  2.915746e+00   

       pock_asa22_st  ...     BLOSUM3.1     BLOSUM4.1     BLOSUM5.1  \
count   3.120000e+02  ...  3.120000e+02  3.120000e+02  3.120000e+02   
mean    1.465752e-15  ... -3.061120e-16 -4.981770e-17 -1.715152e-15   
std     1.001606e+00  ...  1.001606e+00  1.001606e+00  1.001606e+00   
min    -3.079700e+00  ... -3.397914e+00 -3.209078e+00 -2.688531e+00   
25%    -6.112113e-01  ... -5.238429e-01 -6.887405e-01 -6.096362e-01   
50%    -3.949586e-02  ... -1.739576e-01 -1.296583e-01  5.046639e-02   
75%     6.381443e-01  ...  6.900849e-01  6.712171e-01  6.800486e-01   
max     2.739704e+00  ...  2.627780e+00  2.427584e+00  3.010917e+00   

          BLOSUM6.1     BLOSUM7.1     BLOSUM8.1     BLOSUM9.1    BLOSUM10.1  \
count  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02  3.120000e+02   
mean  -5.208932e-10  1.100259e-15 -6.476301e-17 -2.586962e-15  3.917806e-16   
std    1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00  1.001606e+00   
min   -4.425535e+00 -3.394447e+00 -3.327902e+00 -2.811915e+00 -2.402391e+00   
25%   -5.189082e-01 -5.408273e-01 -6.093871e-01 -6.359302e-01 -7.419341e-01   
50%   -1.258063e-01  1.441778e-01 -2.871712e-02 -1.033992e-01  3.491162e-02   
75%    4.918462e-01  4.128514e-01  6.016009e-01  6.979394e-01  6.514358e-01   
max    2.660765e+00  3.470691e+00  3.257280e+00  2.888041e+00  2.727678e+00   

          MSWHIM1.1   MSWHIM2.1  
count  3.120000e+02  312.000000  
mean   1.839696e-16   -0.026578  
std    1.001606e+00    1.001253  
min   -3.156276e+00   -2.863891  
25%   -4.895878e-01   -0.566367  
50%   -1.610016e-01    0.042745  
75%    5.667845e-01    0.427446  
max    2.967846e+00    4.659166  

[8 rows x 186 columns]

In [12]:
model = GradientBoostingRegressor(verbose=0)
cv = RepeatedKFold(n_splits=10, n_repeats=3, random_state=101)
scores = cross_val_score(model, data, Y, scoring='neg_mean_absolute_error', cv=cv, n_jobs=1)
scores = absolute(scores)
print('Mean MAE: %.3f (%.3f)' % (scores.mean(), scores.std()))

Mean MAE: 0.857 (0.147)


In [13]:
# # Polynomial combination of features
# poly = PolynomialFeatures(2)
# data = poly.fit_transform(data)
# dataset = DataFrame(data)
# num_instances = 3
# num_folds = 6
# seed = 4236
# scoring = "neg_mean_absolute_error"
# models = get_models()
# results, names = list(), list()
# for name, model in models.items():
#     scores = evaluate_model(model, data, Y)
#     results.append(scores)
#     names.append(name)
#     print('>%s %.3f (%.3f)' % (name, mean(scores), std(scores)))
#

In [14]:
# pyplot.boxplot(results, labels=names, showmeans=True)
# pyplot.xlabel('Polynomial Degree')
# pyplot.ylabel('Negative Mean Absolute Error')
# pyplot.savefig("Box-poly.jpg")
# pyplot.show()
#

In [15]:
# # define dataset
# X, y = get_dataset()
# # calculate change in number of features
# num_features = list()
# degress = [i for i in range(1, 4)]
# for d in degress:
# 	# create transform
# 	trans = PolynomialFeatures(degree=d)
# 	# fit and transform
# 	data = trans.fit_transform(X)
# 	# record number of features
# 	num_features.append(data.shape[1])
# 	# summarize
# 	print('Degree: %d, Features: %d' % (d, data.shape[1]))
# # plot degree vs number of features
#
#

In [16]:
# z = [1, 2, 3]
# pyplot.plot(degress, num_features)
# pyplot.xlabel('Polynomial Degree')
# pyplot.ylabel('Number of Features')
# for i, txt in enumerate(num_features):
#     pyplot.annotate(txt, (z[i], num_features[i]), textcoords="offset pixels", # how to position the text
#                  xytext=(3,2), # distance from text to points (x,y)
#                  ha='center')
# pyplot.savefig("Number_Of_Features.jpg")
# pyplot.show()
#

In [17]:
# new_df = add_interactions(X)
# scaler = StandardScaler()
# new_df_scaled = scaler.fit_transform(new_df)
# data = pd.DataFrame(new_df_scaled, columns=new_df.columns)
# data

In [18]:
# data_1 = data.iloc[:, :30]
# data_2 = data.iloc[:, 30:60]
# data_3 = data.iloc[:, 60:90]
# data_4 = data.iloc[:, 90:120]
# data_5 = data.iloc[:, 120:]


In [19]:
# data_1.to_csv("preprocessed_data_1.csv", header=True, index=False)
# data_2.to_csv("preprocessed_data_2.csv", header=True, index=False)
# data_3.to_csv("preprocessed_data_3.csv", header=True, index=False)
# data_4.to_csv("preprocessed_data_4.csv", header=True, index=False)
# data_5.to_csv("preprocessed_data_5.csv", header=True, index=False)
data.to_csv("prepocessed_data.csv", header=True, index=False)

In [20]:
from lazypredict.Supervised import LazyRegressor
from sklearn.model_selection import train_test_split
#
X = data
Y


X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=.2, random_state=42)

C:\Users\Nick\AppData\Roaming\Python\Python37\site-packages\sklearn\utils\deprecation.py:143: FutureWarning: The sklearn.utils.testing module is  deprecated in version 0.22 and will be removed in version 0.24. The corresponding classes / functions should instead be imported from sklearn.utils. Anything that cannot be imported from sklearn.utils is now part of the private API.
  warnings.warn(message, FutureWarning)


In [21]:
#fit all models
reg = LazyRegressor(predictions=True)
models, predictions = reg.fit(X_train, X_test, y_train, y_test)

100%|██████████| 42/42 [00:11<00:00,  3.60it/s]


In [22]:
# models = pd.DataFrame(models)
#

In [23]:
models

Adjusted R-Squared  \
Model                                                                              
Lars                          13534755343820335101106535979980391634941907768...   
RANSACRegressor                                                             8.50   
TransformedTargetRegressor                                                  2.22   
LinearRegression                                                            2.22   
GaussianProcessRegressor                                                    1.61   
KernelRidge                                                                 1.59   
PassiveAggressiveRegressor                                                  1.58   
ExtraTreeRegressor                                                          1.54   
DecisionTreeRegressor                                                       1.53   
LassoLars                                                                   1.50   
Lasso                                                                       1.50   
LarsCV                                                                      1.50   
DummyRegressor                                                              1.50   
HuberRegressor                                                              1.50   
Ridge                                                                       1.48   
ElasticNet                                                                  1.42   
LinearSVR                                                                   1.39   
SGDRegressor                                                                1.37   
MLPRegressor                                                                1.37   
KNeighborsRegressor                                                         1.35   
RidgeCV                                                                     1.35   
BaggingRegressor                                                            1.31   
OrthogonalMatchingPursuitCV                                                 1.30   
XGBRegressor                                                                1.29   
LassoLarsCV                                                                 1.28   
OrthogonalMatchingPursuit                                                   1.28   
SVR                                                                         1.28   
ElasticNetCV                                                                1.28   
LassoCV                                                                     1.28   
NuSVR                                                                       1.27   
LassoLarsIC                                                                 1.27   
GeneralizedLinearRegressor                                                  1.26   
TweedieRegressor                                                            1.26   
BayesianRidge                                                               1.26   
RandomForestRegressor                                                       1.26   
AdaBoostRegressor                                                           1.24   
ExtraTreesRegressor                                                         1.23   
LGBMRegressor                                                               1.23   
HistGradientBoostingRegressor                                               1.23   
GradientBoostingRegressor                                                   1.22   

                                                                       R-Squared  \
Model                                                                              
Lars                          -2706951068764067020221307195996078326988381553...   
RANSACRegressor                                                           -14.00   
TransformedTargetRegressor                                                 -1.44   
LinearRegression                                                           -1.44   
GaussianProcessRegressor     

In [24]:
data_preprocessed = pd.concat([X,Y], axis=1)
data_preprocessed.head()
data_preprocessed.to_csv("preprop_and_target.csv", header=True, index=False)

In [30]:
X_train, X_test, y_train, y_test = train_test_split(X,Y, random_state=42, test_size=0.1)
gbr = GradientBoostingRegressor(verbose=0)
gbr.fit(X_train, y_train)
print("Model Accuracy: %.3f")
gbr.score(X_test, y_test)
mse = mean_squared_error(y_test, gbr.predict(X_test))
print("The mse on test set: {:.4f}".format(mse))

Model Accuracy: %.3f
The mse on test set: 1.1169


In [39]:
test_score = np.zeros((params["n_estimators"],), dtype=np.float64)
for i, y_pred in enumerate(reg.staged_predict(X_test)):
    test_score[i] = reg.loss_(y_test, y_pred)

fig = plt.figure(figsize=(6, 6))
plt.subplot(1, 1, 1)
plt.title("Deviance")
plt.plot(
    np.arange(params["n_estimators"]) + 1,
    reg.train_score_,
    "b-",
    label="Training Set Deviance",
)
plt.plot(
    np.arange(params["n_estimators"]) + 1, test_score, "r-", label="Test Set Deviance"
)
plt.legend(loc="upper right")
plt.xlabel("Boosting Iterations")
plt.ylabel("Deviance")
fig.tight_layout()
plt.show()

NameError: name 'params' is not defined

In [29]:
seed = 7
test_size = 0.2

X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=seed)
model = GradientBoostingRegressor(verbose=0)
eval_set = [(X_train, y_train), (X_test, y_test)]
model.fit(X_train, y_train, eval_set=eval_set, verbose=True, early_stopping_rounds=10)
y_pred = model.predict(X_test)
predictions = [value for value in y_pred]
predictions
results = model.evals_result()
epoch = len(results['validation_0']['mae'])
x_axis = range(0, epoch)
# plot log loss
fig, ax = pyplot.subplots()
ax.plot(x_axis, results['validation_0']['mae'], label='Train')
ax.plot(x_axis, results['validation_1']['mae'], label='Test')
ax.legend()
pyplot.ylabel('Mean Absolute Error')
pyplot.title('XGBoost MAE')
pyplot.show()
# plot classification error
fig, ax = pyplot.subplots()
ax.plot(x_axis, results['validation_0']['rmse'], label='Train')
ax.plot(x_axis, results['validation_1']['rmse'], label='Test')
ax.legend()
pyplot.ylabel('Root Mean Square Error')
pyplot.title('XGBoost RMSE')
pyplot.show()

TypeError: fit() got an unexpected keyword argument 'eval_set'

In [ ]:
import xgboost as xgb
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import r2_score
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import fbeta_score, make_scorer
from xgboost.sklearn import XGBRegressor

parameters = {'objective':['reg:squarederror'],
              'booster':['gbtree','gblinear'],
              'learning_rate': [0.001,0.004,0.008,0.01,0.02,0.03,0.04,0.05,0.06,0.07,
                                0.08,0.09,0.1,0.2,0.4,0.6,0.8,1],
              'max_depth': range(1,100,10),
              'min_child_weight': range(5,100,5),
              'colsample_bytree': [0.1,0.2,0.4,0.8,1],
              'n_estimators': range(10,1000,10),
              "reg_alpha"   : [0.1,0.2,0.4,0.6,0.8,1],
              "reg_lambda"  : range(1,10,1),
              "gamma"       : range(1,10,1)}

xgb_model = GradientBoostingRegressor(random_state=30)

grid_obj_xgb = RandomizedSearchCV(xgb_model,parameters, cv=5,n_iter=15,scoring='neg_mean_absolute_error',verbose=5,n_jobs=12)
grid_obj_xgb.fit(X_train, y_train,verbose = 1)

y_pred_train = grid_obj_xgb.predict(X_train)
y_pred_test = grid_obj_xgb.predict(X_test)

err_xgb_train=mean_absolute_error(y_train, y_pred_train, multioutput='raw_values')

In [ ]:
print('\n All results:')
print(grid_obj_xgb.cv_results_)
print('\n Best estimator:')
print(grid_obj_xgb.best_estimator_)
print('\n Best hyperparameters:')
print(grid_obj_xgb.best_params_)
results = pd.DataFrame(grid_obj_xgb.cv_results_)#

In [ ]:
# seed = 7
# test_size = 0.2
#
# X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=seed)
# model = xgb.XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
#              colsample_bynode=1, colsample_bytree=0.9, gamma=3, gpu_id=-1,
#              importance_type='gain', interaction_constraints='',
#              learning_rate=0.003, max_delta_step=0, max_depth=60,
#              min_child_weight=40, monotone_constraints='()',
#              n_estimators=10000, n_jobs=0, num_parallel_tree=1, random_state=30,
#              reg_alpha=1, reg_lambda=5, scale_pos_weight=1, subsample=1,
#              tree_method='exact', validate_parameters=1, verbosity=None)
#
# eval_set = [(X_train, y_train), (X_test, y_test)]
# model.fit(X_train, y_train, eval_metric=["mae", "rmse"], eval_set=eval_set, verbose=True, early_stopping_rounds=10)
# y_pred = model.predict(X_test)
# predictions = [value for value in y_pred]
# predictions
# results = model.evals_result()
# epoch = len(results['validation_0']['mae'])
# x_axis = range(0, epoch)
# # plot log loss
# fig, ax = pyplot.subplots()
# ax.plot(x_axis, results['validation_0']['mae'], label='Train')
# ax.plot(x_axis, results['validation_1']['mae'], label='Test')
# ax.legend()
# pyplot.ylabel('Mean Absolute Error')
# pyplot.title('XGBoost MAE')
# pyplot.show()
# # plot classification error
# fig, ax = pyplot.subplots()
# ax.plot(x_axis, results['validation_0']['rmse'], label='Train')
# ax.plot(x_axis, results['validation_1']['rmse'], label='Test')
# ax.legend()
# pyplot.ylabel('Root Mean Square Error')
# pyplot.title('XGBoost RMSE')
# pyplot.show()

In [ ]:
# from sklearn.model_selection import cross_val_score, KFold
# from sklearn.metrics import mean_absolute_error
#
# scores = []
# cv = KFold(n_splits=5, shuffle=True)
# fig = plt.figure()
# i = 1
# for train, test in cv.split(X_train, y_train):
#     prediction = model.fit(X_train.iloc[train],
#                  y_train.iloc[train]).predict(X_train.iloc[test])
#     true = y_train.iloc[test]
#     score = mean_absolute_error(true, prediction)
#     scores.append(score)
#     plt.scatter(prediction, true, lw=2, alpha=0.3,
#                 label='Fold %d (MAE = %0.2f)' % (i,score))
#     i = i+1
# plt.plot([min(y_train),max(y_train)], [min(y_train),max(y_train)],
#          linestyle='--', lw=2, color='black')
# plt.xlabel('Predicted Value')
# plt.ylabel('Actual Value')
# plt.title('K-Fold Validation')
# plt.legend(prop={"size":10})
# plt.show()
#

In [ ]:
# from sklearn import metrics
# ## Kpi
# print("R2 (explained variance):", round(metrics.r2_score(y_test, predictions), 2))
# print("Mean Absolute Perc Error (Σ(|y-pred|/y)/n):", round(np.mean(np.abs((y_test-predictions)/predictions)), 2))
# print("Mean Absolute Error (Σ|y-pred|/n):", "{:,.0f}".format(metrics.mean_absolute_error(y_test, predictions)))
# print("Root Mean Squared Error (sqrt(Σ(y-pred)^2/n)):", "{:,.0f}".format(np.sqrt(metrics.mean_squared_error(y_test, predictions))))
# ## residuals
# residuals = []
# for i, c in zip(y_test, y_pred):
#     residuals.append(i - c)
#

In [ ]:
# max_error = max(residuals) if abs(max(residuals)) > abs(min(residuals)) else min(residuals)
# max_idx = list(residuals).index(max(residuals)) if abs(max(residuals)) > abs(min(residuals)) else list(residuals).index(min(residuals))
# max_true, max_pred = y_test.iloc[max_idx], y_pred[max_idx]
# print("Max Error:", "{:,.0f}".format(max_error))
#

In [ ]:
# print(y_test.iloc[20] - y_pred[20])
#

In [ ]:
# fig, ax = plt.subplots(nrows=1, ncols=2)
# from statsmodels.graphics.api import abline_plot
# ax[0].scatter(y_pred, y_test, color="black")
# abline_plot(intercept=0, slope=1, color="red", ax=ax[0])
# ax[0].vlines(x=max_pred, ymin=max_true, ymax=max_true-max_error, color='red', linestyle='--', alpha=0.7, label="max error")
# ax[0].grid(True)
# ax[0].set(xlabel="Predicted", ylabel="True", title="Predicted vs True")
# ax[0].legend()
#
# ## Plot predicted vs residuals
# ax[1].scatter(y_pred, residuals, color="red")
# ax[1].vlines(x=max_pred, ymin=0, ymax=max_error, color='black', linestyle='--', alpha=0.7, label="max error")
# ax[1].grid(True)
# ax[1].set(xlabel="Predicted", ylabel="Residuals", title="Predicted vs Residuals")
# ax[1].hlines(y=0, xmin=np.min(y_pred), xmax=np.max(y_pred))
# ax[1].legend()
# plt.savefig("residuals_fit.jpg")
# plt.show()
#

In [ ]:
# import seaborn as sns
# fig, ax = plt.subplots()
# sns.distplot(residuals, color="red", hist=True, kde=True, kde_kws={"shade":True}, ax=ax)
# ax.grid(True)
# ax.set(yticks=[], yticklabels=[], title="Residuals distribution")
# plt.show()
#
#

In [ ]:
# ## Importance
# X_train, X_test, Y_train, Y_test = train_test_split(X, Y, test_size = 0.2)
# # Build the model with the random forest regression algorithm:
# model.fit(X_train, Y_train)
#

In [ ]:
# import shap
#

In [ ]:
# shap_values = shap.TreeExplainer(model).shap_values(X_train)
# shap.summary_plot(shap_values, X_train, plot_type="bar")
#

In [ ]:
# import matplotlib.pyplot as plt
# f = plt.figure()
# shap.summary_plot(shap_values, X_train)
# f.savefig("summary_plot1.png", bbox_inches='tight', dpi=600)